## Alternus Vera
Dataset: Politifact/Liar-Liar dataset(https://www.politifact.com)

Description of the train TSV file format:

- Column 1: the ID of the statement ([ID].json)
- Column 2: the label.
- Column 3: the statement.
- Column 4: the subject(s).
- Column 5: the speaker.
- Column 6: the speaker's job title.
- Column 7: the state info.
- Column 8: the party affiliation.
- Column 9-13: the total credit history count, including the current statement.
  - 9: barely true counts.
  - 10: false counts.
  - 11: half true counts.
  - 12: mostly true counts.
  - 13: pants on fire counts.
- Column 14: the context (venue / location of the speech or statement).

In [2]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
import nltk
from nltk.stem.porter import *
from nltk.corpus import stopwords  
from nltk.stem.porter import PorterStemmer
from sklearn.feature_extraction.text import TfidfVectorizer

In [3]:
df =pd.read_csv('/Users/vidhsharma/Documents/SJSU/Fall18/ML/Lab/fakeNews/liar_dataset/train.tsv', sep='\t')

In [4]:
df.head(10)

file        value                                          statement  \
0   2635.json        FALSE  Says the Annies List political group supports ...   
1  10540.json    half-true  When did the decline of coal start? It started...   
2    324.json  mostly-true  Hillary Clinton agrees with John McCain "by vo...   
3   1123.json        FALSE  Health care reform legislation is likely to ma...   
4   9028.json    half-true  The economic turnaround started at the end of ...   
5  12465.json         TRUE  The Chicago Bears have had more starting quart...   
6   2342.json  barely-true  Jim Dunnam has not lived in the district he re...   
7    153.json    half-true  I'm the only person on this stage who has work...   
8   5602.json    half-true  However, it took $19.5 million in Oregon Lotte...   
9   9741.json  mostly-true  Says GOP primary opponents Glenn Grothman and ...   

                                       topic                    name  \
0                                   abortion            dwayne-bohac   
1         energy,history,job-accomplishments          scott-surovell   
2                             foreign-policy            barack-obama   
3                                health-care            blog-posting   
4                               economy,jobs           charlie-crist   
5                                  education               robin-vos   
6                       candidates-biography  republican-party-texas   
7                                     ethics            barack-obama   
8                                       jobs          oregon-lottery   
9  energy,message-machine-2014,voting-record           duey-stroebel   

                   occupation      state         party  barely true counts  \
0        State representative      Texas    republican                 0.0   
1              State delegate   Virginia      democrat                 0.0   
2                   President   Illinois      democrat                70.0   
3                         NaN        NaN          none                 7.0   
4                         NaN    Florida      democrat                15.0   
5  Wisconsin Assembly speaker  Wisconsin    republican                 0.0   
6                         NaN      Texas    republican                 3.0   
7                   President   Illinois      democrat                70.0   
8                         NaN        NaN  organization                 0.0   
9        State representative  Wisconsin    republican                 0.0   

   false counts  half true counts  mostly true counts  pants on fire counts  \
0           1.0               0.0                 0.0                   0.0   
1           0.0               1.0                 1.0                   0.0   
2          71.0             160.0               163.0                   9.0   
3          19.0               3.0                 5.0                  44.0   
4           9.0              20.0                19.0                   2.0   
5           3.0               2.0                 5.0                   1.0   
6           1.0               1.0                 3.0                   1.0   
7          71.0             160.0               163.0                   9.0   
8           0.0               1.0                 0.0                   1.0   
9           0.0               0.0                 1.0                   0.0   

                                   context   
0                                  a mailer  
1                           a floor speech.  
2                                    Denver  
3                            a news release  
4                       an interview on CNN  
5                 a an online opinion-piece  
6                          a press release.  
7  a Democratic debate in Philadelphia, Pa.  
8                                a website   
9                           an online video

In [5]:
df.shape

(10240, 14)

In [6]:
df.columns

Index(['file', 'value', 'statement', 'topic', 'name', 'occupation', 'state',
       'party', 'barely true counts', 'false counts', 'half true counts',
       'mostly true counts', 'pants on fire counts', 'context '],
      dtype='object')

##### Data exploration

In [7]:
df['state'].value_counts()

Texas                                                1009
Florida                                               997
Wisconsin                                             713
New York                                              657
Illinois                                              556
Ohio                                                  447
Georgia                                               426
Virginia                                              407
Rhode Island                                          369
New Jersey                                            241
Oregon                                                239
Massachusetts                                         206
Arizona                                               182
California                                            159
Washington, D.C.                                      120
Vermont                                                98
Pennsylvania                                           90
New Hampshire 

In [8]:
df['party'].unique()

array(['republican', 'democrat', 'none', 'organization', 'independent',
       'columnist', 'activist', 'talk-show-host', 'libertarian',
       'newsmaker', 'journalist', 'labor-leader', 'state-official',
       'business-leader', 'education-official', 'tea-party-member', nan,
       'green', 'liberal-party-canada', 'government-body', 'Moderate',
       'democratic-farmer-labor', 'ocean-state-tea-party-action',
       'constitution-party'], dtype=object)

In [9]:
df.loc[df['topic']=='health-care']

file        value  \
3       1123.json        FALSE   
14      8705.json  barely-true   
25     10215.json        FALSE   
85      2044.json    half-true   
92      2020.json  mostly-true   
165     4504.json  barely-true   
248    11772.json        FALSE   
314     8308.json  barely-true   
350     9031.json        FALSE   
389     5631.json        FALSE   
434     9434.json  barely-true   
442     5629.json        FALSE   
516     3097.json         TRUE   
541     8510.json   pants-fire   
582     2328.json    half-true   
612     1100.json  mostly-true   
619     7788.json    half-true   
707     2302.json    half-true   
731     1630.json  mostly-true   
768     1149.json        FALSE   
772     1509.json  mostly-true   
878    11576.json    half-true   
915    13424.json        FALSE   
929     4512.json        FALSE   
955      786.json        FALSE   
997     3712.json  mostly-true   
1001     262.json  barely-true   
1035    9984.json    half-true   
1038    5651.json        FALSE   
1046    4125.json        FALSE   
...           ...          ...   
9525    8926.json    half-true   
9534    8431.json        FALSE   
9553    1723.json  barely-true   
9569    8593.json        FALSE   
9581    1751.json        FALSE   
9594    5598.json        FALSE   
9673    8313.json    half-true   
9701    1300.json        FALSE   
9720    8512.json   pants-fire   
9727    1127.json    half-true   
9759    8459.json  barely-true   
9776    4465.json  barely-true   
9798     730.json    half-true   
9804    1205.json        FALSE   
9817    1256.json         TRUE   
9843     155.json        FALSE   
9856    1023.json        FALSE   
9872    1166.json  barely-true   
9875    2303.json    half-true   
9882    3680.json  mostly-true   
9896    8330.json  mostly-true   
9954    3070.json        FALSE   
9975    3762.json    half-true   
9985    1281.json         TRUE   
10000   1536.json  mostly-true   
10005   1176.json         TRUE   
10061   1126.json   pants-fire   
10122   8627.json    half-true   
10207   6178.json        FALSE   
10214   4216.json        FALSE   

                                               statement        topic  \
3      Health care reform legislation is likely to ma...  health-care   
14     Most of the (Affordable Care Act) has already ...  health-care   
25                 I dont know who (Jonathan Gruber) is.  health-care   
85     In Rick Perrys Texas, we import nurses ... fro...  health-care   
92     The insurance commissioner cant do squat about...  health-care   
165    Says Rick Perry wrote a letter supporting Hill...  health-care   
248    We now have driven (health care) costs down to...  health-care   
314    The American people support defunding Obamacar...  health-care   
350    Most young Americans right now, theyre not cov...  health-care   
389    Says Congressman Bill Pascrell voted to remove...  health-care   
434    Jason Carter supports using Georgia tax dollar...  health-care   
442    New federal projections estimate that the heal...  health-care   
516    Texas leads the nation in the percentage of re...  health-care   
541    What we said was, you can keep (your plan) if ...  health-care   
582    Charlie Crist has six different positions on O...  health-care   
612    14,000 Americans . . . lose their health insur...  health-care   
619    The Affordable Care Act is bringing the cost o...  health-care   
707    We spend more money on health care per capita ...  health-care   
731    The American people will be appalled to learn ...  health-care   
768    We spend twice as much per capita on health ca...  health-care   
772    One of the most recent polls said 75 percent o...  health-care   
878    The United States is the only major country on...  health-care   
915    Prior to Obamacare here in Wisconsin, 95 perce...  health-care   
929    If we had been on Obamacare and a bureaucrat w...  health-care   
955    Barack Obama's plan calls for "mandates and fi...  health-care   
997   

In [10]:
df.isnull().sum()

file                       0
value                      0
statement                  0
topic                      2
name                       2
occupation              2897
state                   2208
party                      2
barely true counts         2
false counts               2
half true counts           2
mostly true counts         2
pants on fire counts       2
context                  102
dtype: int64

### Data Cleaning
    Tokenizing: converting a document to its atomic elements.
    Stopping: removing meaningless words.
    Stemming: merging words that are equivalent in meaning.

In [14]:
df1 =df.drop(columns=['file','value' ,'barely true counts', 'false counts',
       'half true counts', 'mostly true counts', 'pants on fire counts',])

In [16]:
print (df1)

                                               statement  \
0      Says the Annies List political group supports ...   
1      When did the decline of coal start? It started...   
2      Hillary Clinton agrees with John McCain "by vo...   
3      Health care reform legislation is likely to ma...   
4      The economic turnaround started at the end of ...   
5      The Chicago Bears have had more starting quart...   
6      Jim Dunnam has not lived in the district he re...   
7      I'm the only person on this stage who has work...   
8      However, it took $19.5 million in Oregon Lotte...   
9      Says GOP primary opponents Glenn Grothman and ...   
10     For the first time in history, the share of th...   
11     Since 2000, nearly 12 million Americans have s...   
12     When Mitt Romney was governor of Massachusetts...   
13     The economy bled $24 billion due to the govern...   
14     Most of the (Affordable Care Act) has already ...   
15     In this last election in November

In [18]:
raw =df1[['statement']]
raw[:5]
final=raw.values.T.tolist()
print (len(final[0]))

10240


In [19]:
nltk.download('stopwords')

[nltk_data] Downloading package stopwords to
[nltk_data]     /Users/vidhsharma/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


True

In [20]:
## porter stemmer
def textProcessing(doc):
    process = re.sub('[^a-zA-Z]', ' ',doc) 
    process = process.lower()
    process = process.split()
    ps = PorterStemmer()
    process = [ps.stem(word) for word in process if not word in set(stopwords.words('english'))]
    process = ' '.join(process)
    return process

In [21]:
print('original document: ')
words = []
for word in final:
    words.append(word)
print (words)



original document: 
[['Says the Annies List political group supports third-trimester abortions on demand.', 'When did the decline of coal start? It started when natural gas took off that started to begin in (President George W.) Bushs administration.', 'Hillary Clinton agrees with John McCain "by voting to give George Bush the benefit of the doubt on Iran."', 'Health care reform legislation is likely to mandate free sex change surgeries.', 'The economic turnaround started at the end of my term.', 'The Chicago Bears have had more starting quarterbacks in the last 10 years than the total number of tenured (UW) faculty fired during the last two decades.', 'Jim Dunnam has not lived in the district he represents for years now.', "I'm the only person on this stage who has worked actively just last year passing, along with Russ Feingold, some of the toughest ethics reform since Watergate.", 'However, it took $19.5 million in Oregon Lottery funds for the Port of Newport to eventually land the 

In [22]:
nltk.download('stopwords')

[nltk_data] Downloading package stopwords to
[nltk_data]     /Users/vidhsharma/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


True

In [24]:
result =[]
for i in final[0]:
    result.append(textProcessing(i))
print (result)

['say anni list polit group support third trimest abort demand', 'declin coal start start natur ga took start begin presid georg w bush administr', 'hillari clinton agre john mccain vote give georg bush benefit doubt iran', 'health care reform legisl like mandat free sex chang surgeri', 'econom turnaround start end term', 'chicago bear start quarterback last year total number tenur uw faculti fire last two decad', 'jim dunnam live district repres year', 'person stage work activ last year pass along russ feingold toughest ethic reform sinc waterg', 'howev took million oregon lotteri fund port newport eventu land new noaa marin oper center pacif', 'say gop primari oppon glenn grothman joe leibham cast compromis vote cost million higher electr cost', 'first time histori share nation popular vote margin smaller latino vote margin', 'sinc nearli million american slip middl class poverti', 'mitt romney governor massachusett didnt slow rate growth govern actual cut', 'economi bled billion due

### tokenization the words

In [25]:
from nltk.tokenize import RegexpTokenizer
tokenizer = RegexpTokenizer(r'\w+')

In [27]:
final=[]
for i in result:
    tokens = tokenizer.tokenize(i)
    final.append(tokens)
print (final)



[['say', 'anni', 'list', 'polit', 'group', 'support', 'third', 'trimest', 'abort', 'demand'], ['declin', 'coal', 'start', 'start', 'natur', 'ga', 'took', 'start', 'begin', 'presid', 'georg', 'w', 'bush', 'administr'], ['hillari', 'clinton', 'agre', 'john', 'mccain', 'vote', 'give', 'georg', 'bush', 'benefit', 'doubt', 'iran'], ['health', 'care', 'reform', 'legisl', 'like', 'mandat', 'free', 'sex', 'chang', 'surgeri'], ['econom', 'turnaround', 'start', 'end', 'term'], ['chicago', 'bear', 'start', 'quarterback', 'last', 'year', 'total', 'number', 'tenur', 'uw', 'faculti', 'fire', 'last', 'two', 'decad'], ['jim', 'dunnam', 'live', 'district', 'repres', 'year'], ['person', 'stage', 'work', 'activ', 'last', 'year', 'pass', 'along', 'russ', 'feingold', 'toughest', 'ethic', 'reform', 'sinc', 'waterg'], ['howev', 'took', 'million', 'oregon', 'lotteri', 'fund', 'port', 'newport', 'eventu', 'land', 'new', 'noaa', 'marin', 'oper', 'center', 'pacif'], ['say', 'gop', 'primari', 'oppon', 'glenn', 'g

### adding all the sentence token's in one list

In [34]:
import itertools
flat=itertools.chain.from_iterable(final)
text = list(flat)
print (type(text))

<class 'list'>


In [36]:
from gensim import corpora, models

In [37]:
dictionary = corpora.Dictionary(final)
print (dictionary)

Dictionary(7696 unique tokens: ['abort', 'anni', 'demand', 'group', 'list']...)


In [38]:
import numpy as np
final=np.asarray(final)
raw1 = np.concatenate(final).ravel().tolist()
type(raw1)

list

### Bag of words

In [39]:
dictionary.filter_extremes(no_below=20, no_above=0.5, keep_n=100000)
bow_corpus = [dictionary.doc2bow(result) for result in final]
print (bow_corpus[50])



[(4, 1), (34, 1), (90, 1), (91, 1), (93, 1), (275, 1), (276, 1), (277, 1), (278, 1)]


### TF-IDF on Bag of words

In [41]:
from gensim import corpora, models

tfidf = models.TfidfModel(bow_corpus)
corpus_tfidf = tfidf[bow_corpus]

In [56]:
from pprint import pprint

for doc in corpus_tfidf:
    pprint(doc)
    break

[(0, 0.35904583507755133),
 (1, 0.43205352296640565),
 (2, 0.490320729707899),
 (3, 0.4306640399228395),
 (4, 0.12019203984807553),
 (5, 0.2874852011836854),
 (6, 0.40179104146231087)]


#### Sentiment Analysis

In [59]:
from vaderSentiment.vaderSentiment import SentimentIntensityAnalyzer

analyser = SentimentIntensityAnalyzer()

In [61]:
def sentiment_analyzer_scores(sentence):
    score = analyser.polarity_scores(sentence)
    print("{:-<40} {}".format(sentence, str(score)))

In [72]:
for i in df['statement']:
    result = (sentiment_analyzer_scores(i))
    print (result)
    

Says the Annies List political group supports third-trimester abortions on demand. {'neg': 0.115, 'neu': 0.692, 'pos': 0.192, 'compound': 0.25}
None
When did the decline of coal start? It started when natural gas took off that started to begin in (President George W.) Bushs administration. {'neg': 0.0, 'neu': 0.902, 'pos': 0.098, 'compound': 0.3612}
None
Hillary Clinton agrees with John McCain "by voting to give George Bush the benefit of the doubt on Iran." {'neg': 0.107, 'neu': 0.687, 'pos': 0.206, 'compound': 0.3182}
None
Health care reform legislation is likely to mandate free sex change surgeries. {'neg': 0.0, 'neu': 0.606, 'pos': 0.394, 'compound': 0.7579}
None
The economic turnaround started at the end of my term. {'neg': 0.0, 'neu': 1.0, 'pos': 0.0, 'compound': 0.0}
None
The Chicago Bears have had more starting quarterbacks in the last 10 years than the total number of tenured (UW) faculty fired during the last two decades. {'neg': 0.12, 'neu': 0.836, 'pos': 0.043, 'compound': 

None
Says abortion doctors are flying into this state, performing abortions and flying out. {'neg': 0.0, 'neu': 1.0, 'pos': 0.0, 'compound': 0.0}
None
Speaker Gingrich for 20 years supported a federal individual mandate for health insurance. {'neg': 0.0, 'neu': 0.827, 'pos': 0.173, 'compound': 0.3182}
None
There have been at least 100 shootings each year [Angel Taveras] has been mayor of Providence. {'neg': 0.0, 'neu': 1.0, 'pos': 0.0, 'compound': 0.0}
None
Maurice Ferre says Kendrick Meek has voted 98.6 percent of the time with the Democrat party. {'neg': 0.0, 'neu': 0.847, 'pos': 0.153, 'compound': 0.4019}
None
Weve created more jobs in the United States than every other advanced economy combined since I came into office. {'neg': 0.0, 'neu': 0.688, 'pos': 0.312, 'compound': 0.7003}
None
One in four inmates is an illegal immigrant. {'neg': 0.34, 'neu': 0.66, 'pos': 0.0, 'compound': -0.5574}
None
Wisconsin is dead last in income growth among midwestern states during Gov. Scott Walkers 

China owns about 29 percent of (the U.S.) debt. {'neg': 0.238, 'neu': 0.762, 'pos': 0.0, 'compound': -0.3612}
None
Chris Sununu supported Obamas Common Core agenda, taking away local control of our schools. {'neg': 0.0, 'neu': 0.85, 'pos': 0.15, 'compound': 0.3182}
None
(President Barack Obama) said unemployment was never gonna go over 8 percent if we passed the stimulus plan. {'neg': 0.153, 'neu': 0.847, 'pos': 0.0, 'compound': -0.4404}
None
Gwinnett County government has made significant cutbacks in staffing. {'neg': 0.0, 'neu': 0.816, 'pos': 0.184, 'compound': 0.2023}
None
Says the Constitution specifically states the Congress shall write legislation for immigration policy, so Barack Obama lacks the authority to defer the deportation of young illegal immigrants. {'neg': 0.186, 'neu': 0.772, 'pos': 0.042, 'compound': -0.6705}
None
Crime rises in communities with casinos. {'neg': 0.412, 'neu': 0.588, 'pos': 0.0, 'compound': -0.5423}
None
Americans spend 6.1 billion hours a year comply

None
Says Eric Cantor was the co-author of the House GOP principles on immigration reform. Both the New York Times and the Washington Postsaid that thatcaptured the essence of what was in the Senate immigration bill. {'neg': 0.0, 'neu': 1.0, 'pos': 0.0, 'compound': 0.0}
None
Wisconsins 6th congressional district has more manufacturing jobs than almost any other in the nation. {'neg': 0.0, 'neu': 1.0, 'pos': 0.0, 'compound': 0.0}
None
I lost my health insurance and my doctor because of Obamacare. {'neg': 0.204, 'neu': 0.796, 'pos': 0.0, 'compound': -0.3182}
None
As far as standing committees, we have 10 fewer standing committees. So weve saved the state about a quarter-of-a-million dollars through the reduction of the standing committees. {'neg': 0.0, 'neu': 0.89, 'pos': 0.11, 'compound': 0.4728}
None
(Obamas) entire national security team, including his secretary of state, said we want to arm and train and equip (Syrian rebel forces), and he made the unilateral decision to turn them do

None
Im not one for name calling.------------ {'neg': 0.0, 'neu': 1.0, 'pos': 0.0, 'compound': 0.0}
None
Says Sen. Pat Toomey even tried to shut down the federal government in order to eliminate funding for Planned Parenthood. {'neg': 0.0, 'neu': 1.0, 'pos': 0.0, 'compound': 0.0}
None
Wisconsin has one of the most progressive tax codes in the country. {'neg': 0.0, 'neu': 1.0, 'pos': 0.0, 'compound': 0.0}
None
During the year Kagan barred military recruiters from Harvard Law School's Office of Career Services, "military recruiting actually went up." {'neg': 0.0, 'neu': 1.0, 'pos': 0.0, 'compound': 0.0}
None
ISIS reaches about 100 million people a day through social media. {'neg': 0.0, 'neu': 0.882, 'pos': 0.118, 'compound': 0.0516}
None
Texas added more jobs in 2010 than any other state. {'neg': 0.0, 'neu': 1.0, 'pos': 0.0, 'compound': 0.0}
None
In the primary election, a right-wing group spent more than $100,000,000 to support Supreme Court Justice Rebecca Bradley. {'neg': 0.0, 'neu': 

...

Tim Kaine wants to thwart right-to-work reform measures in Midwest battleground states. {'neg': 0.197, 'neu': 0.803, 'pos': 0.0, 'compound': -0.4019}
None
New Virginia regulations on abortion clinics provide the same sanitary environment we expect of dental offices. {'neg': 0.0, 'neu': 1.0, 'pos': 0.0, 'compound': 0.0}
None
On average, women make 77 cents for every dollar men make. {'neg': 0.0, 'neu': 1.0, 'pos': 0.0, 'compound': 0.0}
None
Says Charlie Crist signed the nations harshest marijuana laws. {'neg': 0.328, 'neu': 0.672, 'pos': 0.0, 'compound': -0.5994}
None
We are the most generous in New England and New England is known for its generosity toward its welfare recipients. {'neg': 0.0, 'neu': 0.723, 'pos': 0.277, 'compound': 0.7841}
None
I used my line-item veto authority to veto $360 million dollars in special interest spending, so that our budget this year ... is still smaller than the fiscal year 2008 and 2009 budgets signed by my predecessor. {'neg': 0.0, 'neu': 0.825, 'pos'

None
Today in America, we have more people in jail than any other country on Earth. {'neg': 0.0, 'neu': 1.0, 'pos': 0.0, 'compound': 0.0}
None
The Muslim Brotherhood has openly stated they want to declare war on Israel. {'neg': 0.241, 'neu': 0.679, 'pos': 0.08, 'compound': -0.5574}
None
On financial reform, there is "a million dollars being spent, per congressman, in lobbying expenses on this issue. (The) industry has four lobbyists per member of the House and Senate working on this." {'neg': 0.039, 'neu': 0.961, 'pos': 0.0, 'compound': -0.0772}
None
Elena Kagan "violated the law of the United States at various points" with her opposition to military recruiters. {'neg': 0.153, 'neu': 0.721, 'pos': 0.126, 'compound': -0.1531}
None
Sixty million Americans depend on Social Security, and one-third of all the seniors in America depend on Social Security for 90 percent of their income. {'neg': 0.0, 'neu': 0.827, 'pos': 0.173, 'compound': 0.5859}
None
Already we've identified $2 trillion in d

None
Farouk is on fire.---------------------- {'neg': 0.444, 'neu': 0.556, 'pos': 0.0, 'compound': -0.34}
None
Says Patrick Murphy was named one of Americas least effective congressmen. {'neg': 0.203, 'neu': 0.797, 'pos': 0.0, 'compound': -0.3724}
None
Obamacare adds trillions to our deficits and to our national debt. {'neg': 0.2, 'neu': 0.8, 'pos': 0.0, 'compound': -0.3612}
None
Frankly, (Hillary Clinton) doesnt do very well with women. {'neg': 0.202, 'neu': 0.798, 'pos': 0.0, 'compound': -0.2572}
None
Says Democratic U.S. Senate candidate Russ Feingold voted over 250 times to raise taxes. {'neg': 0.0, 'neu': 1.0, 'pos': 0.0, 'compound': 0.0}
None
The gun industry isthe only business in America that is wholly protected from any kind of liability. {'neg': 0.21, 'neu': 0.654, 'pos': 0.136, 'compound': -0.1513}
None
Your tellers were paid kickbacks for directing elderly consumers from ... safe deposits to risky ones. {'neg': 0.096, 'neu': 0.749, 'pos': 0.155, 'compound': 0.2732}
None
Say

Says union bosses bused protesters to aCentral Florida education protest. {'neg': 0.328, 'neu': 0.672, 'pos': 0.0, 'compound': -0.4404}
None
Says that at a campaign rally President Barack Obama spent so much time screaming at a protester, and frankly it was a disgrace. {'neg': 0.252, 'neu': 0.748, 'pos': 0.0, 'compound': -0.7239}
None
On transparency in dealing with the Republican Party of Florida's financial issues. {'neg': 0.0, 'neu': 0.803, 'pos': 0.197, 'compound': 0.4019}
None
Says a drug test can be performed for just $4 or $5. {'neg': 0.0, 'neu': 1.0, 'pos': 0.0, 'compound': 0.0}
None
Oregon House Republicans jobs plan could generate more than 50,000 jobs over five years. {'neg': 0.0, 'neu': 1.0, 'pos': 0.0, 'compound': 0.0}
None
Says that before Rick Perry became governor, only 4 percent of our total labor force was a minimum wage job ... Today, that number has more than doubled (to) 9.5 percent. {'neg': 0.0, 'neu': 0.956, 'pos': 0.044, 'compound': 0.0772}
None
When Hillary Cli

Says Rick Scott pled the Fifth 75 times to avoid jail for Medicare fraud. {'neg': 0.333, 'neu': 0.667, 'pos': 0.0, 'compound': -0.7184}
None
Over the time that President Obama has been in office, we have lost 2.5 million free enterprise system jobs, and, yet, 500,000 federal government jobs have been added. {'neg': 0.073, 'neu': 0.823, 'pos': 0.104, 'compound': 0.25}
None
Brock Turners early release will be a regular occurrence if Prop. 57 passes. {'neg': 0.0, 'neu': 1.0, 'pos': 0.0, 'compound': 0.0}
None
Taxes are lower on families than theyve been probably in the last 50 years. {'neg': 0.145, 'neu': 0.855, 'pos': 0.0, 'compound': -0.296}
None
As a state representative, David Cicilline argued against Megans Law and voted against mandatory registration of sex offenders. {'neg': 0.246, 'neu': 0.69, 'pos': 0.064, 'compound': -0.5719}
None
This guy didn't even support Ronald Reagan. {'neg': 0.273, 'neu': 0.727, 'pos': 0.0, 'compound': -0.3089}
None
Says Rick Scott is letting Duke (Energy)

### LDA Model on bag of words

In [43]:
import gensim
from gensim.utils import simple_preprocess
from gensim.parsing.preprocessing import STOPWORDS
import numpy as np
np.random.seed(2018)

In [44]:
lda_model = gensim.models.ldamodel.LdaModel(bow_corpus, num_topics=10, id2word = dictionary, passes=2)

In [45]:
print (lda_model)

LdaModel(num_terms=968, num_topics=10, decay=0.5, chunksize=2000)


In [47]:
for idx, topic in lda_model.print_topics(-1):
    print('Topic: {} \nWords: {}'.format(idx, topic))

Topic: 0 
Words: 0.126*"percent" + 0.041*"tax" + 0.027*"rate" + 0.024*"year" + 0.017*"incom" + 0.017*"pay" + 0.015*"american" + 0.015*"sinc" + 0.014*"top" + 0.013*"say"
Topic: 1 
Words: 0.049*"job" + 0.025*"state" + 0.022*"peopl" + 0.017*"creat" + 0.016*"get" + 0.016*"offic" + 0.015*"new" + 0.013*"health" + 0.013*"insur" + 0.013*"busi"
Topic: 2 
Words: 0.053*"vote" + 0.031*"say" + 0.026*"bill" + 0.022*"democrat" + 0.021*"support" + 0.018*"u" + 0.018*"john" + 0.016*"allow" + 0.016*"even" + 0.016*"mccain"
Topic: 3 
Words: 0.033*"say" + 0.025*"illeg" + 0.025*"immigr" + 0.024*"texa" + 0.023*"trump" + 0.022*"state" + 0.021*"one" + 0.020*"wage" + 0.020*"donald" + 0.016*"law"
Topic: 4 
Words: 0.053*"year" + 0.025*"state" + 0.023*"million" + 0.018*"peopl" + 0.018*"two" + 0.018*"got" + 0.016*"last" + 0.015*"work" + 0.013*"wisconsin" + 0.013*"everi"
Topic: 5 
Words: 0.051*"presid" + 0.039*"obama" + 0.024*"ever" + 0.021*"say" + 0.021*"state" + 0.019*"time" + 0.018*"bush" + 0.017*"debt" + 0.015*"f

10 topics:
- tax rate
- job
- voting for bill 
- immigration
- President Obama
- school fund
- tax on health care

#### Score calculation

In [48]:
for index, score in sorted(lda_model[bow_corpus[4310]], key=lambda tup: -1*tup[1]):
    print("\nScore: {}\t \nTopic: {}".format(score, lda_model.print_topic(index, 10)))


Score: 0.47892361879348755	 
Topic: 0.053*"vote" + 0.031*"say" + 0.026*"bill" + 0.022*"democrat" + 0.021*"support" + 0.018*"u" + 0.018*"john" + 0.016*"allow" + 0.016*"even" + 0.016*"mccain"

Score: 0.19224534928798676	 
Topic: 0.056*"say" + 0.022*"republican" + 0.020*"budget" + 0.020*"secur" + 0.020*"state" + 0.018*"billion" + 0.017*"cut" + 0.016*"rick" + 0.016*"clinton" + 0.016*"democrat"

Score: 0.17535533010959625	 
Topic: 0.051*"presid" + 0.039*"obama" + 0.024*"ever" + 0.021*"say" + 0.021*"state" + 0.019*"time" + 0.018*"bush" + 0.017*"debt" + 0.015*"first" + 0.015*"unit"

Score: 0.1073104590177536	 
Topic: 0.045*"say" + 0.034*"school" + 0.034*"fund" + 0.028*"public" + 0.027*"romney" + 0.025*"state" + 0.023*"student" + 0.020*"educ" + 0.020*"mitt" + 0.015*"would"


### LDA Model on tf -idf

In [51]:
lda_model_tfidf  = gensim.models.ldamodel.LdaModel(corpus_tfidf, num_topics=10, id2word = dictionary, passes=2)

In [52]:
print (lda_model)

LdaModel(num_terms=968, num_topics=10, decay=0.5, chunksize=2000)


In [53]:
for idx, topic in lda_model.print_topics(-1):
    print('Topic: {} \nWords: {}'.format(idx, topic))

Topic: 0 
Words: 0.126*"percent" + 0.041*"tax" + 0.027*"rate" + 0.024*"year" + 0.017*"incom" + 0.017*"pay" + 0.015*"american" + 0.015*"sinc" + 0.014*"top" + 0.013*"say"
Topic: 1 
Words: 0.049*"job" + 0.025*"state" + 0.022*"peopl" + 0.017*"creat" + 0.016*"get" + 0.016*"offic" + 0.015*"new" + 0.013*"health" + 0.013*"insur" + 0.013*"busi"
Topic: 2 
Words: 0.053*"vote" + 0.031*"say" + 0.026*"bill" + 0.022*"democrat" + 0.021*"support" + 0.018*"u" + 0.018*"john" + 0.016*"allow" + 0.016*"even" + 0.016*"mccain"
Topic: 3 
Words: 0.033*"say" + 0.025*"illeg" + 0.025*"immigr" + 0.024*"texa" + 0.023*"trump" + 0.022*"state" + 0.021*"one" + 0.020*"wage" + 0.020*"donald" + 0.016*"law"
Topic: 4 
Words: 0.053*"year" + 0.025*"state" + 0.023*"million" + 0.018*"peopl" + 0.018*"two" + 0.018*"got" + 0.016*"last" + 0.015*"work" + 0.013*"wisconsin" + 0.013*"everi"
Topic: 5 
Words: 0.051*"presid" + 0.039*"obama" + 0.024*"ever" + 0.021*"say" + 0.021*"state" + 0.019*"time" + 0.018*"bush" + 0.017*"debt" + 0.015*"f

10 topics:
- tax
- sex
- wage
- college 
- train
- job
- health care
- Donald Trump
- oil tax

#### Score calculation

In [54]:
for index, score in sorted(lda_model_tfidf[bow_corpus[4310]], key=lambda tup: -1*tup[1]):
    print("\nScore: {}\t \nTopic: {}".format(score, lda_model_tfidf.print_topic(index, 10)))




Score: 0.5462357401847839	 
Topic: 0.024*"health" + 0.023*"care" + 0.018*"insur" + 0.013*"compani" + 0.012*"walker" + 0.012*"job" + 0.012*"scott" + 0.012*"oil" + 0.012*"ga" + 0.011*"employe"

Score: 0.296714723110199	 
Topic: 0.014*"largest" + 0.013*"food" + 0.013*"john" + 0.012*"democrat" + 0.011*"board" + 0.011*"presid" + 0.011*"say" + 0.010*"member" + 0.010*"despit" + 0.010*"vote"

Score: 0.1031959056854248	 
Topic: 0.020*"job" + 0.016*"state" + 0.014*"percent" + 0.013*"wisconsin" + 0.012*"new" + 0.012*"measur" + 0.012*"california" + 0.012*"year" + 0.011*"florida" + 0.011*"lose"
